In [5]:
# 必要なライブラリをインポートします
import numpy as np
from keras.datasets import mnist
from keras.models import Sequential, Model
from keras.layers import Dense, Flatten, Reshape, LeakyReLU, Dropout, Input
from keras.optimizers import Adam
from keras import initializers
from tqdm import tqdm
import matplotlib.pyplot as plt

In [6]:
# MNISTデータセットをロードします
(X_train, y_train), (X_test, y_test) = mnist.load_data()
X_train = (X_train.astype(np.float32) - 127.5)/127.5
X_train = X_train.reshape(60000, 784)

random_dim = 100

In [7]:
# 生成器を作成します
def create_generator():
    generator = Sequential()
    generator.add(Dense(256, input_dim=random_dim, kernel_initializer=initializers.RandomNormal(stddev=0.02)))
    generator.add(LeakyReLU(0.2))
    generator.add(Dense(512))
    generator.add(LeakyReLU(0.2))
    generator.add(Dense(1024))
    generator.add(LeakyReLU(0.2))
    generator.add(Dense(784, activation='tanh'))
    return generator

In [8]:
# 判別器を作成します
def create_discriminator():
    discriminator = Sequential()
    discriminator.add(Dense(1024, input_dim=784, kernel_initializer=initializers.RandomNormal(stddev=0.02)))
    discriminator.add(LeakyReLU(0.2))
    discriminator.add(Dropout(0.3))
    discriminator.add(Dense(512))
    discriminator.add(LeakyReLU(0.2))
    discriminator.add(Dropout(0.3))
    discriminator.add(Dense(256))
    discriminator.add(LeakyReLU(0.2))
    discriminator.add(Dropout(0.3))
    discriminator.add(Dense(1, activation='sigmoid'))
    discriminator.compile(loss='binary_crossentropy', optimizer=Adam())
    return discriminator

In [10]:
# GANを作成します
def create_gan(discriminator, random_dim, generator):
    discriminator.trainable = False
    gan_input = Input(shape=(random_dim,))
    x = generator(gan_input)
    gan_output = discriminator(x)
    gan = Model(inputs=gan_input, outputs=gan_output)
    gan.compile(loss='binary_crossentropy', optimizer=Adam())
    return gan

In [12]:
# GANを学習します
def train_gan(gan, discriminator, generator, random_dim, epochs=1, batch_size=128):
    for e in range(1, epochs+1):
        for _ in tqdm(range(batch_size)):
            noise = np.random.normal(0, 1, size=[batch_size, random_dim])
            image_batch = X_train[np.random.randint(0, X_train.shape[0], size=batch_size)]

            # ステップ1: 偽の画像を生成します
            generated_images = generator.predict(noise)
            X = np.concatenate([image_batch, generated_images])

            # ステップ2: ラベルを作成します
            y_dis = np.zeros(2*batch_size)
            y_dis[:batch_size] = 0.9

            # ステップ3: 判別器を訓練します
            discriminator.trainable = True
            discriminator.train_on_batch(X, y_dis)

            # ステップ4: 生成器の訓練データとラベルを作成します
            noise = np.random.normal(0, 1, size=[batch_size, random_dim])
            y_gen = np.ones(batch_size)

            # ステップ5: 生成器を訓練します
            discriminator.trainable = False
            gan.train_on_batch(noise, y_gen)

        if e == 1 or e % 20 == 0:
            print(f"Epoch {e} of {epochs}")

In [13]:
# 生成器、判別器、GANを作成します
generator = create_generator()
discriminator = create_discriminator()
gan = create_gan(discriminator, random_dim, generator)

In [14]:
# GANを学習します
train_gan(gan, discriminator, generator, random_dim, epochs=50, batch_size=128)

  0%|          | 0/128 [00:00<?, ?it/s]

4/4 [==============================] - 0s 3ms/step


2023-07-05 10:48:07.210695: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [256]
	 [[{{node Placeholder/_1}}]]
2023-07-05 10:48:07.704221: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [128]
	 [[{{node Placeholder/_1}}]]
  1%|          | 1/128 [00:01<02:39,  1.26s/it]

4/4 [==============================] - 0s 2ms/step


2023-07-05 10:48:08.257379: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [256]
	 [[{{node Placeholder/_1}}]]
2023-07-05 10:48:08.282723: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [128]
	 [[{{node Placeholder/_1}}]]
  2%|▏         | 2/128 [00:01<01:12,  1.73it/s]

...

4/4 [==============================] - 0s 5ms/step


2023-07-05 11:01:48.046292: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [256]
	 [[{{node Placeholder/_1}}]]
2023-07-05 11:01:48.076895: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_1' with dtype float and shape [128]
	 [[{{node Placeholder/_1}}]]
 34%|███▍      | 44/128 [00:08<00:23,  3.58it/s]

1/4 [======>.......................] - ETA: 0s

 34%|███▍      | 44/128 [00:08<00:16,  5.02it/s]


KeyboardInterrupt: 

In [ ]:
# GANを学習します
train_gan(gan, discriminator, generator, random_dim, epochs=50, batch_size=128)

# 新たな手書き数字を生成します
num_examples = 100
noise = np.random.normal(0, 1, size=[num_examples, random_dim])
generated_images = generator.predict(noise)

# 生成した画像を表示します
plt.figure(figsize=(10, 10))
for i in range(num_examples):
    plt.subplot(10, 10, i+1)
    plt.imshow(generated_images[i].reshape(28, 28), cmap='gray')
    plt.axis('off')
plt.tight_layout()
plt.show()
